# Adaptive Asset Allocation Model 

Our universe (basket) of stocks: 
- VTI (Vanguard Total Stock Market Index Fund)
- VXUS (Vanguard Total International Stock Index Fund)
- VNQ (Vanguard Real Estate Index Fund Investor Shares)
- BND (Vanguard Total Bond Market Index Fund Investor Shares)
- GLD (SPDR Gold Trust)
- EFA (iShares MSCI EAFE ETF Europe Australia Far East) 
- TLT (iShares 20 Plus Year Treasury Bond ETF)
- IEF (iShares 7-10 Year Treasury Bond ETF)
- QQQ (Tech ETF)


Choose the top 4 ETF's with the greatest returns in the past 180 trading days. 
Take these 3 ETF's, analyze its standard deviations and covariances, and use these values to generate the Markowitz **Min-Variance Portfolio** derived from Modern Portfolio Theory

In [1]:
import numpy as np
import pandas as pd
import random
import plotly.express as px
from yahoo_fin.stock_info import *
import matplotlib.pyplot as plt

In [2]:
basket = ['VTI', 'VXUS', 'VNQ', 'BND', 'GLD', 'EFA', 'TLT', 'IEF', 'QQQ']
total_return_window = 180
volatility_window = 20
nlargest = 4

In [3]:
df_data = {}
for stock_ticker in basket: 
    data = get_data(stock_ticker)
    adj_closed = data['adjclose'][-total_return_window:]
    df_data[stock_ticker] = adj_closed
    
df = pd.DataFrame(df_data)

In [4]:
window_returns = np.log(df.iloc[-1]) - np.log(df.iloc[0])
nlargest = list(window_returns.nlargest(4).index)
nlargest

['VNQ', 'QQQ', 'TLT', 'VTI']

In [5]:
returns = df[nlargest].pct_change()
returns_cov_normalized = returns[-volatility_window:].apply(lambda x: np.log(1+x)).cov()
returns_corr_normalized = returns[-volatility_window:].apply(lambda x: np.log(1+x)).corr()
returns_std = returns.apply(lambda x: np.log(1+x)).std()

In [6]:
#Returns Standard Deviations
returns_std


VNQ    0.008937
QQQ    0.009273
TLT    0.008429
VTI    0.007571
dtype: float64

In [7]:
#Returns Correlations
returns_corr_normalized

VNQ       QQQ       TLT       VTI
VNQ  1.000000  0.603088 -0.332252  0.861033
QQQ  0.603088  1.000000 -0.234628  0.855657
TLT -0.332252 -0.234628  1.000000 -0.378578
VTI  0.861033  0.855657 -0.378578  1.000000

In [8]:
#Returns Covariances 
returns_cov_normalized

VNQ       QQQ       TLT       VTI
VNQ  0.000147  0.000082 -0.000048  0.000099
QQQ  0.000082  0.000125 -0.000031  0.000091
TLT -0.000048 -0.000031  0.000141 -0.000043
VTI  0.000099  0.000091 -0.000043  0.000091

In [9]:
port_returns = []
port_volatility = []
port_weights = []

num_assets = len(returns.columns)
num_portfolios = 10000
individual_rets = window_returns[nlargest]

## Analyze custom portfolio weight
Keep it commented out when not in use

In [10]:
# for port in range(1): 
#     weights = [1,0,0,0]
#     port_weights.append(weights)
    
#     rets = np.dot(weights, individual_rets)
#     port_returns.append(rets)
    
#     var = returns_cov_normalized.mul(weights, axis=0).mul(weights, axis=1).sum().sum()
#     sd = np.sqrt(var)
#     ann_sd = sd * np.sqrt(256)
#     port_volatility.append(ann_sd)

## Analyze random portfolios and their efficient frontier

In [11]:
for port in range(num_portfolios): 
    weights = np.random.random(num_assets)
    weights = weights/np.sum(weights)
    port_weights.append(weights)
    
    rets = np.dot(weights, individual_rets)
    port_returns.append(rets)
    
    var = returns_cov_normalized.mul(weights, axis=0).mul(weights, axis=1).sum().sum()
    sd = np.sqrt(var)
    ann_sd = sd * np.sqrt(256)
    port_volatility.append(ann_sd)

## Build DataFrame of portfolios

In [12]:
    
data = {'Returns': port_returns, 'Volatility': port_volatility}
hover_data = []
for counter, symbol in enumerate(nlargest): 
    data[symbol] = [w[counter] for w in port_weights]
    hover_data.append(symbol)
    
portfolios_V1 = pd.DataFrame(data)
portfolios_V1.head()

Returns  Volatility       VNQ       QQQ       TLT       VTI
0  0.149911    0.102422  0.203038  0.143791  0.334409  0.318762
1  0.163747    0.111710  0.354085  0.222540  0.288047  0.135328
2  0.154935    0.119062  0.051129  0.399720  0.215233  0.333918
3  0.156058    0.163375  0.438081  0.072919  0.001958  0.487042
4  0.154135    0.104055  0.318666  0.091265  0.355394  0.234675

## Efficient Frontier

In [13]:
import plotly.express as px
fig = px.scatter(portfolios_V1, x="Volatility", y="Returns", hover_data=hover_data)
fig.show()

## Min Variance Portfolio

In [14]:
min_var_portfolio = portfolios_V1.iloc[portfolios_V1['Volatility'].idxmin()]
min_var_portfolio

Returns       0.132507
Volatility    0.094790
VNQ           0.006972
QQQ           0.045071
TLT           0.421474
VTI           0.526483
Name: 5046, dtype: float64

In [15]:
PORTFOLIO_VALUE = 35000
min_var_portfolio[nlargest] * PORTFOLIO_VALUE

VNQ      244.010385
QQQ     1577.488796
TLT    14751.580002
VTI    18426.920816
Name: 5046, dtype: float64

## Max Sharpe Ratio Portfolio

In [16]:
max_sharpe_portfolio = portfolios_V1.iloc[(portfolios_V1['Returns'] / portfolios_V1['Volatility']).idxmax()]
max_sharpe_portfolio

Returns       0.166681
Volatility    0.104780
VNQ           0.302323
QQQ           0.299654
TLT           0.395741
VTI           0.002281
Name: 3157, dtype: float64

In [17]:
max_sharpe_portfolio[nlargest] * PORTFOLIO_VALUE

VNQ    10581.320369
QQQ    10487.905757
TLT    13850.934914
VTI       79.838960
Name: 3157, dtype: float64